In [48]:
import pdb
import os
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'

In [84]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
import torch.optim as optim
from torchtext.vocab import GloVe
from torchtext.data import Field, BucketIterator
from torchtext.data.metrics import bleu_score
import spacy
import fasttext.util
from nltk.translate.bleu_score import sentence_bleu, corpus_bleu

In [50]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [51]:
#Reading files

with open('trainen.txt', encoding='utf8') as f:
    eng_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('trainta.txt', encoding='utf8') as f:
    tamil_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('deven.txt', encoding='utf8') as f:
    eng_test = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('devta.txt', encoding='utf8') as f:
    tamil_test = list(map(lambda x: x.rstrip(), f.readlines()))
    
embedding_glove = GloVe(name='6B', dim=100)

spacy_en = spacy.load('en_core_web_sm')

def tokenize_en(text):
    return [tok.text for tok in spacy_en.tokenizer(text)]

stop_words = [',','.','?','!',')','(',':',']','[','$','#','&','%','--']
ENG = Field(tokenize = tokenize_en, init_token='sos', eos_token = 'eos', lower=True, stop_words=stop_words)
processed_eng_train = list(map(lambda x: ENG.preprocess(x), eng_train))
processed_eng_test = list(map(lambda x: ENG.preprocess(x), eng_test))

ENG.build_vocab(processed_eng_train, vectors=embedding_glove)

In [52]:
def preprocess(processed_eng):
    
    #function to return the numericalized version of the tokenized sentences
    X = []
    for tokenized_sentence in processed_eng:
        int_sequence = [2]  #first element is the SOS token 
        for token in tokenized_sentence:
            int_sequence.append(ENG.vocab.stoi[token])
        int_sequence.append(3) #last element is the EOS token
        X.append(int_sequence)
    
    return X

# X_train and X_test are lists of lists with the integer sequences for a given sentence
X_train = preprocess(processed_eng_train)
X_test = preprocess(processed_eng_test)

In [53]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

# Same thing for Tamil sentences
TAM = Tokenizer()
TAM.fit_on_texts(tamil_train)
Y_train = TAM.texts_to_sequences(tamil_train)
Y_test = TAM.texts_to_sequences(tamil_test)

#adding EOS token
_ = [y.append(0) for y in Y_train]
_ = [y.append(0) for y in Y_test]

In [54]:
TAM.index_word[0] = 'EOS'
TAM.index_word[len(TAM.index_word)] = 'SOS'

In [55]:
source_vocab_size = len(ENG.vocab)
target_vocab_size = len(TAM.index_word)
print(source_vocab_size)
print(target_vocab_size)

9723
18670


In [56]:
# Code to load a model and save embeddings as a numpy array for later use
# ft = fasttext.load_model('cc.ta.300.bin')
# tamil_embedding = torch.zeros(target_vocab_size, 300)
# for i in range(target_vocab_size):
#     tamil_embedding[i] = torch.FloatTensor(ft.get_word_vector(TAM.index_word[i]))

# X = tamil_embedding.numpy()
# np.save('tam_embed.npy', X)

In [57]:
# loading pretrained weights from numpy file
tamil_embedding = np.load('tam_embed.npy')
tamil_embedding = torch.from_numpy(tamil_embedding)

In [58]:
class Encoder(nn.Module):
    
    def __init__(self, embed_size, hidden_size, ENG):
        
        super(Encoder, self).__init__()
        self.embed_size = embed_size
        self.hidden_size = hidden_size
        self.embed = nn.Embedding.from_pretrained(ENG.vocab.vectors)
        self.lstm = nn.LSTM(embed_size, hidden_size)
        
    def forward(self, x, enc_hidden):
        
        embedded_x = self.embed(x)  # Ts x 100
        enc_output, enc_hidden = self.lstm(embedded_x.unsqueeze(1), enc_hidden)
        return enc_output, enc_hidden

In [59]:
class Decoder(nn.Module):
    
    def __init__(self, hidden_size, n_classes, embeddings):
        
        super(Decoder, self).__init__()
        self.embed_size = embeddings.shape[1]
        self.hidden_size = hidden_size
        self.embed = nn.Embedding.from_pretrained(embeddings)
        self.lstm = nn.LSTM(embeddings.shape[1], hidden_size)
        self.fc = nn.Linear(hidden_size, n_classes)
        self.logsoftmax = nn.LogSoftmax(dim=1)
    
    def forward(self, x, dec_hidden):
        
        dec_output, dec_hidden = self.lstm(self.embed(x).view(1,1,-1), dec_hidden)
        dec_output = self.logsoftmax(self.fc(dec_output[0]))
        
        return dec_output, dec_hidden

In [60]:
def loss_per_pair(source_sentence, target_sentence, enc_obj, dec_obj, enc_optimiser, dec_optimiser, loss_fn):
    
    Ts = source_sentence.size(-1)
    Tt = target_sentence.size(-1)
    enc_hidden = (torch.zeros(1, 1, enc_obj.hidden_size, device=device), torch.zeros(1, 1, enc_obj.hidden_size, device=device))
    
    enc_optimiser.zero_grad()
    dec_optimiser.zero_grad()
    
    loss_val = 0
    
    # source_sentence is a 1-D tensor of size Ts
    enc_output, enc_hidden = enc_obj(source_sentence, enc_hidden)
    
    dec_input = torch.tensor([[target_vocab_size-1]], device=device)  #SOS token
    
    # first hidden(and cell) state of decoder is made the final hidden(and cell) state of the encoder
    dec_hidden = enc_hidden
    
    for i in range(Tt):
        
        dec_output, dec_hidden = dec_obj(dec_input, dec_hidden)
        _ , index = dec_output.topk(1)
        #dec_input = index.squeeze().detach()
        #print(TAM.index_word[dec_input.item()])
            
        target_word = torch.cuda.LongTensor([target_sentence[i].item()])
        dec_input = target_word
        
        loss_val += loss_fn(dec_output, target_word)
        
        if dec_input.item() == 0:
            break

    loss_val.backward()
    
    nn.utils.clip_grad_norm_(enc_obj.parameters(), 0.5)
    nn.utils.clip_grad_norm_(dec_obj.parameters(), 0.5)

    enc_optimiser.step()
    dec_optimiser.step()

    return loss_val.item()/Tt

In [72]:
def train_model(sources, targets, enc_obj, dec_obj, lr=0.001, mom=0.9):
    
    loss_fn = nn.NLLLoss()
#     enc_optimiser = optim.SGD(enc_obj.parameters(), lr=lr, momentum=mom)
#     dec_optimiser = optim.SGD(dec_obj.parameters(), lr=lr, momentum=mom)
    enc_optimiser = optim.Adam(enc_obj.parameters())
    dec_optimiser = optim.Adam(dec_obj.parameters())
    
    max_epochs = 100
    old_loss = np.inf
    indices = [i for i in range(len(sources))]
    
    for epoch in range(max_epochs):
        
        # shuffling the input data manually at the start of every new epoch
        np.random.shuffle(indices)
        sources = list(np.array(sources)[indices])
        targets = list(np.array(targets)[indices])
        
        running_loss = 0.0
        num_sentences = len(sources)
        
        for i in range(num_sentences):
            source_sentence = torch.cuda.LongTensor(sources[i])
            target_sentence = torch.cuda.LongTensor(targets[i])

            loss = loss_per_pair(source_sentence, target_sentence, enc_obj, dec_obj, enc_optimiser, dec_optimiser, loss_fn)
            running_loss += loss

            if i%int(num_sentences*0.1)==0:
                print("Epoch", epoch+1, ":", (i/int(num_sentences*0.1))*10,'% done')
                print("Current loss:", running_loss)
                
        print('\nEpoch', epoch+1,"\n")
        print("Encoder obj lstm wts sum=", torch.sum(enc_obj.lstm.weight_ih_l0))
        print("Encoder obj lstm bias sum=", torch.sum(enc_obj.lstm.bias_ih_l0))
        print('Decoder obj emb wts sum=', torch.sum(dec_obj.embed.weight.data))
        print('Decoder obj lstm wts sum=', torch.sum(dec_obj.lstm.weight_ih_l0.data))
        print('Decoder obj lstm bias sum=', torch.sum(dec_obj.lstm.bias_ih_l0.data))
        print('Decoder obj linear wts sum=', torch.sum(dec_obj.fc.weight.data))
        print('Decoder obj linear bias sum=', torch.sum(dec_obj.fc.bias.data))
        
        
        if abs(running_loss-old_loss)/running_loss < 1e-3:
            print('Converged')
            break
    
        old_loss = running_loss

    print("Finished Training")

In [73]:
embedding_size = 100
hidden_size = 150
encoder = Encoder(embedding_size, hidden_size, ENG).to(device)
decoder = Decoder(hidden_size, target_vocab_size, tamil_embedding).to(device)
encoder.load_state_dict(torch.load('q3_enc_wts.pt'))
decoder.load_state_dict(torch.load('q3_dec_wts.pt'))
train_model(X_train, Y_train, encoder, decoder)

Epoch 1 : 0.0 % done
Current loss: 2.736166000366211
Epoch 1 : 10.0 % done
Current loss: 15179.950704202667
Epoch 1 : 20.0 % done
Current loss: 30113.808992164137
Epoch 1 : 30.0 % done
Current loss: 45139.35974092485
Epoch 1 : 40.0 % done
Current loss: 60078.32609498928
Epoch 1 : 50.0 % done
Current loss: 74927.16337716507
Epoch 1 : 60.0 % done
Current loss: 90119.15472381577
Epoch 1 : 70.0 % done
Current loss: 105221.09821226519
Epoch 1 : 80.0 % done
Current loss: 120648.5092664632
Epoch 1 : 90.0 % done
Current loss: 136027.33748164764
Epoch 1 : 100.0 % done
Current loss: 151577.12903188623

Epoch 1 

Encoder obj lstm wts sum= tensor(333.3644, device='cuda:0', grad_fn=<SumBackward0>)
Encoder obj lstm bias sum= tensor(0.1440, device='cuda:0', grad_fn=<SumBackward0>)
Decoder obj emb wts sum= tensor(-6130.7305, device='cuda:0')
Decoder obj lstm wts sum= tensor(116.8900, device='cuda:0')
Decoder obj lstm bias sum= tensor(16.7644, device='cuda:0')
Decoder obj linear wts sum= tensor(6168.70

Decoder obj emb wts sum= tensor(-6130.7305, device='cuda:0')
Decoder obj lstm wts sum= tensor(289.6894, device='cuda:0')
Decoder obj lstm bias sum= tensor(82.7759, device='cuda:0')
Decoder obj linear wts sum= tensor(-176879.6094, device='cuda:0')
Decoder obj linear bias sum= tensor(-293770.2500, device='cuda:0')
Epoch 9 : 0.0 % done
Current loss: 6.735423496791294
Epoch 9 : 10.0 % done
Current loss: 7011.50826463487
Epoch 9 : 20.0 % done
Current loss: 14464.119036394917
Epoch 9 : 30.0 % done
Current loss: 22314.766628971756
Epoch 9 : 40.0 % done
Current loss: 30412.344293081842
Epoch 9 : 50.0 % done
Current loss: 38967.43765391774
Epoch 9 : 60.0 % done
Current loss: 47909.07585950497
Epoch 9 : 70.0 % done
Current loss: 57171.76142210543
Epoch 9 : 80.0 % done
Current loss: 66349.18880659473
Epoch 9 : 90.0 % done
Current loss: 75727.94436760094
Epoch 9 : 100.0 % done
Current loss: 85387.3647010528

Epoch 9 

Encoder obj lstm wts sum= tensor(510.6301, device='cuda:0', grad_fn=<SumBackward

Epoch 16 : 40.0 % done
Current loss: 22195.700775004385
Epoch 16 : 50.0 % done
Current loss: 28503.71723709747
Epoch 16 : 60.0 % done
Current loss: 35136.83877730169
Epoch 16 : 70.0 % done
Current loss: 42165.556998983404
Epoch 16 : 80.0 % done
Current loss: 49298.57923243049
Epoch 16 : 90.0 % done
Current loss: 56704.44097691121
Epoch 16 : 100.0 % done
Current loss: 64316.7080384485

Epoch 16 

Encoder obj lstm wts sum= tensor(631.6022, device='cuda:0', grad_fn=<SumBackward0>)
Encoder obj lstm bias sum= tensor(23.6237, device='cuda:0', grad_fn=<SumBackward0>)
Decoder obj emb wts sum= tensor(-6130.7305, device='cuda:0')
Decoder obj lstm wts sum= tensor(283.8724, device='cuda:0')
Decoder obj lstm bias sum= tensor(99.8805, device='cuda:0')
Decoder obj linear wts sum= tensor(186033., device='cuda:0')
Decoder obj linear bias sum= tensor(-399894., device='cuda:0')
Epoch 17 : 0.0 % done
Current loss: 4.691117720170454
Epoch 17 : 10.0 % done
Current loss: 4782.454261522559
Epoch 17 : 20.0 % d

Epoch 24 : 10.0 % done
Current loss: 3922.7354134521106
Epoch 24 : 20.0 % done
Current loss: 8058.809893787962
Epoch 24 : 30.0 % done
Current loss: 12584.703032552812
Epoch 24 : 40.0 % done
Current loss: 17342.472873549315
Epoch 24 : 50.0 % done
Current loss: 22388.953860920443
Epoch 24 : 60.0 % done
Current loss: 27585.814313700765
Epoch 24 : 70.0 % done
Current loss: 32949.53219095397
Epoch 24 : 80.0 % done
Current loss: 38735.583564165
Epoch 24 : 90.0 % done
Current loss: 44667.984172508994
Epoch 24 : 100.0 % done
Current loss: 50804.139641605456

Epoch 24 

Encoder obj lstm wts sum= tensor(704.2689, device='cuda:0', grad_fn=<SumBackward0>)
Encoder obj lstm bias sum= tensor(24.3231, device='cuda:0', grad_fn=<SumBackward0>)
Decoder obj emb wts sum= tensor(-6130.7305, device='cuda:0')
Decoder obj lstm wts sum= tensor(332.9218, device='cuda:0')
Decoder obj lstm bias sum= tensor(115.2480, device='cuda:0')
Decoder obj linear wts sum= tensor(615531.1250, device='cuda:0')
Decoder obj linea

Epoch 31 : 100.0 % done
Current loss: 44115.32301334632

Epoch 31 

Encoder obj lstm wts sum= tensor(843.7924, device='cuda:0', grad_fn=<SumBackward0>)
Encoder obj lstm bias sum= tensor(28.5822, device='cuda:0', grad_fn=<SumBackward0>)
Decoder obj emb wts sum= tensor(-6130.7305, device='cuda:0')
Decoder obj lstm wts sum= tensor(367.1803, device='cuda:0')
Decoder obj lstm bias sum= tensor(129.7510, device='cuda:0')
Decoder obj linear wts sum= tensor(990657.3125, device='cuda:0')
Decoder obj linear bias sum= tensor(-554698.5625, device='cuda:0')
Epoch 32 : 0.0 % done
Current loss: 0.18902587890625
Epoch 32 : 10.0 % done
Current loss: 3464.781661851442
Epoch 32 : 20.0 % done
Current loss: 6948.462674100123
Epoch 32 : 30.0 % done
Current loss: 10813.079701265358
Epoch 32 : 40.0 % done
Current loss: 15049.295348530559
Epoch 32 : 50.0 % done
Current loss: 19479.902097331484
Epoch 32 : 60.0 % done
Current loss: 23820.51579231136
Epoch 32 : 70.0 % done
Current loss: 28522.021647443355
Epoch 32

Epoch 39 : 10.0 % done
Current loss: 3014.500387231538
Epoch 39 : 20.0 % done
Current loss: 6409.749912671657
Epoch 39 : 30.0 % done
Current loss: 10047.242482579133
Epoch 39 : 40.0 % done
Current loss: 13878.533860282178
Epoch 39 : 50.0 % done
Current loss: 17773.375491670977
Epoch 39 : 60.0 % done
Current loss: 21818.866339118602
Epoch 39 : 70.0 % done
Current loss: 26063.647537977256
Epoch 39 : 80.0 % done
Current loss: 30552.630074030356
Epoch 39 : 90.0 % done
Current loss: 35048.71131165465
Epoch 39 : 100.0 % done
Current loss: 39896.4982523994

Epoch 39 

Encoder obj lstm wts sum= tensor(889.2454, device='cuda:0', grad_fn=<SumBackward0>)
Encoder obj lstm bias sum= tensor(29.3529, device='cuda:0', grad_fn=<SumBackward0>)
Decoder obj emb wts sum= tensor(-6130.7305, device='cuda:0')
Decoder obj lstm wts sum= tensor(444.7838, device='cuda:0')
Decoder obj lstm bias sum= tensor(144.4777, device='cuda:0')
Decoder obj linear wts sum= tensor(1396549.2500, device='cuda:0')
Decoder obj line

KeyboardInterrupt: 

In [78]:
torch.save(encoder.state_dict(), 'q3_enc_wts.pt')
torch.save(decoder.state_dict(), 'q3_dec_wts.pt')
# Add these two lines after declaring the encoder and decoder objects and before train_model()
#train_model(X_train, Y_train, encoder, decoder)

In [23]:
def test_loss(sources, targets, enc_obj, dec_obj):
    
    loss_fn = nn.NLLLoss()
    num_sentences = len(sources)
    total_loss = 0
        
    for i in range(num_sentences):

        with torch.no_grad():

            source_sentence = torch.cuda.LongTensor(sources[i])
            target_sentence = torch.cuda.LongTensor(targets[i])
            Ts = source_sentence.size(-1)
            Tt = target_sentence.size(-1)
            enc_hidden = (torch.zeros(1, 1, enc_obj.hidden_size, device=device), torch.zeros(1, 1, enc_obj.hidden_size, device=device))
            
            loss_val = 0
            
            enc_output, enc_hidden = enc_obj(source_sentence, enc_hidden)

            dec_input = torch.tensor([[target_vocab_size-1]], device=device)  #SOS token

            # first hidden state of decoder is made the final hidden state of the encoder and cell state is initialised with zeros
            dec_hidden = enc_hidden

            for i in range(Tt):

                dec_output, dec_hidden = dec_obj(dec_input, dec_hidden)
                _ , index = dec_output.topk(1)
                dec_input = index.squeeze().detach()
                if index.item() == 0:
                    break

                target_word = torch.cuda.LongTensor([target_sentence[i].item()])

                loss_val += loss_fn(dec_output, target_word)
            
            total_loss += loss_val.item()/Tt
    
    return total_loss

In [24]:
# this test loss is for 500 sentences
test_loss(X_test, Y_test, encoder, decoder)

739.9332675518084

In [81]:
def eval_bleu(enc_obj, dec_obj, source_sentence, target, target_vocab_dict):
    
    # function to return the BLEU score for a single sentence 
    
    with torch.no_grad():
        
        Ts = source_sentence.size(-1)
        enc_hidden = (torch.zeros(1, 1, enc_obj.hidden_size, device=device), torch.zeros(1, 1, enc_obj.hidden_size, device=device))

        enc_output, enc_hidden = enc_obj(source_sentence, enc_hidden)

        dec_input = torch.tensor([[target_vocab_size-1]], device=device)  # SOS

        dec_hidden = enc_hidden

        predicted = []

        for i in range(60):
            dec_output, dec_hidden = dec_obj(dec_input, dec_hidden)
            _ , index = dec_output.data.topk(1)
            if index.item() == 0:
                #decoded_words.append('<EOS>')
                break
            else:
                predicted.append(target_vocab_dict[index.item()])

            dec_input = index.squeeze().detach()

    target = [target]
    print("Predicted:",predicted)
    print("Target:",target)
    
    return predicted, target

In [82]:
def evaluate_model(enc_obj, dec_obj, source_test, target_test, target_vocab_dict):
    
    # returns the average bleu score for the model with the given test data
    
    n = len(source_test)
    all_pred = []
    all_targets = []
    for i in range(n):
        source_sentence = torch.cuda.LongTensor(source_test[i])
        target = [target_vocab_dict[x] for x in target_test[i][:-1]]
        pred, trg = eval_bleu(enc_obj, dec_obj, source_sentence, target, target_vocab_dict)
        all_pred.append(pred)
        all_targets.append(trg)
    
    corp_bleu1 = corpus_bleu(all_targets, all_pred, weights=(1.0, 0, 0, 0))
    corp_bleu2 = corpus_bleu(all_targets, all_pred, weights=(0.5, 0.5, 0, 0))
    corp_bleu3 = corpus_bleu(all_targets, all_pred, weights=(1/3, 1/3, 1/3, 0))
    corp_bleu4 = corpus_bleu(all_targets, all_pred)
    
    return corp_bleu1, corp_bleu2, corp_bleu3, corp_bleu4

In [86]:
evaluate_model(encoder, decoder, X_train, Y_train, TAM.index_word)

Predicted: ['நாம்', 'எங்கே', 'போகிறோம்', 'என்று']
Target: [['நாம்', 'எங்கே', 'போகிறோம்', 'என்று']]
Predicted: ['அவர்கள்', 'terraforming']
Target: [['அவர்கள்', 'terraforming']]
Predicted: ['நீங்கள்', 'சார்லஸ்டன்', 'என்னை', 'கிடைக்கும்']
Target: [['நீங்கள்', 'சார்லஸ்டன்', 'என்னை', 'கிடைக்கும்', 'துடைக்க', 'வேண்டும்']]
Predicted: ['இல்லை', 'அவர்', 'என்', 'அப்பா', 'இல்லை']
Target: [['இல்லை', 'அவர்', 'என்', 'அப்பா', 'இல்லை']]
Predicted: ['அவளை', 'வாருங்கள்', 'நாங்கள்']
Target: [['நான்', 'ஞாயிறுகளில்', 'அவளை', 'நாம்', 'மற்ற', 'கூறினார்']]
Predicted: ['கோள்களின்', 'பொறியியல்', 'பொறியியல்']
Target: [['கோள்களின்', 'பொறியியல்']]
Predicted: ['90', 'சதவிகிதம்', 'தானாம்', 'dr', 'brand']
Target: [['90', 'சதவிகிதம்', 'தானாம்', 'dr', 'brand']]
Predicted: ['இந்த', 'அனுப்பினார்']
Target: [['இந்த', 'அனுப்பினார்']]
Predicted: ['அது']
Target: [['அது']]
Predicted: ['நான்', 'தங்க', 'வரை', 'இருந்து', 'ஒன்றும்', 'முடியாது']
Target: [['நான்', 'யோசிக்காமல்', 'விளையாட்டுகளில்', 'அதிகம்', 'இல்லை']]
Predi

Target: [['ஜேக்கப்ஸ்']]
Predicted: ['இருந்தன']
Target: [['மேட்']]
Predicted: ['நீங்கள்', 'அதை', 'செய்ய', 'முடியும்']
Target: [['நீங்கள்', 'செய்ய', 'முடியும்', 'மகிழ்ச்சியளிக்கிறது']]
Predicted: ['சர்']
Target: [['சர்']]
Predicted: ['இருந்தன']
Target: [['இருந்தன']]
Predicted: ['இருந்தன']
Target: [['இருந்தன']]
Predicted: ['தொலைபேசி', 'மோதிரங்கள்']
Target: [['தொலைபேசி', 'மோதிரங்கள்']]
Predicted: ['இரண்டு', 'நாட்களுக்கு', 'மூன்று']
Target: [['இரண்டு', 'நாட்களுக்கு', 'மூன்று']]
Predicted: ['டாக்டர்', 'கார்னெல்', 'என்று']
Target: [['டாக்டர்', 'கார்னெல்', 'என்று']]
Predicted: ['இந்த', 'மக்கள்', 'மக்கள்']
Target: [['இந்த', 'மக்கள்', 'அனைத்து']]
Predicted: ['நீங்கள்', 'செய்ய', 'வாழ்த்துக்கள்']
Target: [['நீங்கள்', 'செய்ய', 'வாழ்த்துக்கள்']]
Predicted: ['பின்னர்', 'அவர்கள்', 'காதலி', 'போலீஸ்', 'பார்க்கலாம்']
Target: [['பின்னர்', 'அதே', 'போலீஸ்', 'நிலையத்திற்கு', 'என்று', 'காதலி', 'அழைக்க']]
Predicted: ['நான்', 'தேவாலயத்தில்', 'போகிறேன்']
Target: [['நான்', 'தேவாலயத்தில்', 'போகிறேன்']]
Pre

Predicted: ['பிறகு', 'இயல்பு', 'எடுத்துக்கொண்டார்']
Target: [['பிறகு', 'இயல்பு', 'எடுத்துக்கொண்டார்']]
Predicted: ['நீ', 'என்ன', 'நினைக்கிறாய்']
Target: [['நீ', 'என்ன', 'நினைக்கிறாய்']]
Predicted: ['இப்போ', 'என்ன']
Target: [['இப்போ', 'என்ன', 'விஷயம்']]
Predicted: ['யாருடைய', 'அதிகாரத்தை']
Target: [['யாருடைய', 'அதிகாரத்தை']]
Predicted: ['இரண்டு', 'மரியாதைங்குறது', 'நமக்காக', 'இஸ்தார்', 'பெண்', 'வேண்டும்', 'என்று', 'நீங்கள்', 'விரும்பவில்லை']
Target: [['இரண்டு', 'மரியாதைங்குறது', 'தானா', 'பெறனும்', 'கேட்டுப்பெறக்கூடாது', 'என்னை', 'நீக்குறதுக்கு', 'உனக்கு', 'சந்தர்ப்பம்', 'கிடைக்கல']]
Predicted: ['நான்', 'என்ன', 'செய்கிறீர்கள்']
Target: [['நான்', 'என்ன', 'வேண்டும்', 'என்று', 'என்னிடம்', 'கொடுத்தார்']]
Predicted: ['உங்கள்', 'ஒவ்வொரு', 'முறையும்', 'ஒவ்வொரு', 'பெயர்', 'பெயர்']
Target: [['ஒவ்வொரு', 'முறையும்', 'யாரோ', 'உங்கள்', 'பெயரை', 'குறிப்பிடுகிறார்']]
Predicted: ['ஒரு', 'உணர்வு']
Target: [['ஒரு', 'உணர்வு']]
Predicted: ['அந்த', 'பையன்', 'தவிர']
Target: [['அந்த', 'பையன்', 'தவிர']]


Target: [['மனித', 'இனம்', 'பூமியில்', 'பிறந்தால்', 'பூமியில்', 'தான்', 'இறக்க', 'வேண்டும்', 'என்றில்லை']]
Predicted: ['எனது', 'முதலாளி', 'உடனே', 'பழைய', 'சிவப்பு', 'புணர்கிறேன்']
Target: [['நீ', 'எனக்கு', 'என்', 'அம்மா', 'அதே', 'பழைய', 'அழுதுவிட்டு', 'கதை']]
Predicted: ['இல்லை', 'போக', 'வேண்டாம்']
Target: [['அவளை', 'விட்டு', 'செல்லாதே', 'முட்டாள்']]
Predicted: ['அவர்', 'அவள்', 'உள்ளே', 'என்ன', 'அது', 'எல்லா', 'பணம்', 'தேவைப்படுகிறது']
Target: [['அவர்', 'அவரது', 'பணப்பையை', 'திருடி', 'அதை', 'திரும்பி', 'வருகிறார்', 'இல்லை']]
Predicted: ['இது', 'செல்லம்', 'நீங்கள்']
Target: [['இது', 'செல்லம்', 'நீ', 'தான்']]
Predicted: ['அவர்களை', 'கொட்டு']
Target: [['அவர்களை', 'கொட்டு', 'விட', 'மிகவும்', 'அல்ல', 'நீங்கள்', 'என்று', 'இல்லை']]
Predicted: ['மெடிக்காகவும்பணியாற்றிவந்தார்']
Target: [['மெடிக்காகவும்பணியாற்றிவந்தார்']]
Predicted: ['ஆஸ்பத்திரிக்கு']
Target: [['ஆஸ்பத்திரிக்கு', 'போகலாம்']]
Predicted: ['5', '000', 'ஆண்டுகள்', 'அவர்', 'எப்போதும்', 'இருக்க', 'வேண்டும்']
Target: [['5', 'கிராண்ட்

Predicted: ['உன்னை', 'திருமணம்', 'மூலம்', '20', 'வினாடிகள்']
Target: [['மற்றும்', 'ஒருவேளை', 'நீங்கள்', 'இயக்க', 'வேண்டும்', 'நான்', '25', 'என்று']]
Predicted: ['நான்', 'எங்கே', 'போக', 'வேண்டும்', 'என்று', 'ஆனால்', 'நான்']
Target: [['நான்', 'நான்', 'உங்களுக்கு', 'ஏனெனில்', 'செல்லலாம்']]
Predicted: ['அவர்கள்', 'யார்']
Target: [['அவர்கள்', 'யார்']]
Predicted: ['நான்', 'இங்கே', 'இருக்கிறேன்']
Target: [['நான்', 'இங்கு', 'இருக்கிறேன்']]
Predicted: ['இந்த', 'மணி', 'நேரத்தில்', 'தொந்திரவு']
Target: [['இந்த', 'மணி', 'நேரத்தில்', 'தொந்திரவு', 'மன்னிக்கவும்']]
Predicted: ['case', 'உங்களுக்காக', 'பார்த்து']
Target: [['மேலும்', 'வழிமுறை', 'காத்திருங்கள்']]
Predicted: ['நீங்கள்', 'இறந்த']
Target: [['நீங்கள்', 'இறந்த']]
Predicted: ['அந்த', 'எண்களை', 'இருக்கிறது']
Target: [['அந்த', 'எண்களை', 'பெறுக']]
Predicted: ['twin1']
Target: [['twin1']]
Predicted: ['எல்லாம்இடையேபிடித்துவிட்டேன்']
Target: [['எல்லாம்இடையேபிடித்துவிட்டேன்']]
Predicted: ['ஏன்குறைந்த', 'இனிப்பு', 'தேர்', 'ஆடாதே']
Target: [['ஏன்குற

...

Predicted: ['ஆம்', 'நீங்கள்', 'அங்கு', 'செய்வேன்', 'ஏன்', 'இது', 'நீங்கள்', 'நினைக்கிறீர்களா']
Target: [['ஆமாம்', 'நீ', 'ஏன்', 'ல்', 'அழைத்து', 'நாம்', 'இல்லை']]
Predicted: ['ஆனால்', 'என்', 'பிறந்தநாள்', 'என்று']
Target: [['ஆனால்', 'இன்று', 'என்', 'பிறந்தநாள்']]
Predicted: ['இங்கே', 'வா', 'அத', 'எடுக்காத']
Target: [['இங்கே', 'வா', 'அத', 'எடுக்காத']]
Predicted: ['நிறுத்து']
Target: [['நிறுத்து']]
Predicted: ['அங்கே']
Target: [['நான்', 'அங்கே', 'இருப்பேன்']]
Predicted: ['என்னால', 'வரேன்']
Target: [['நான்', 'மீது', 'வைக்கனும்']]
Predicted: ['உங்கள்', 'முடி']
Target: [['உங்கள்', 'முடி']]
Predicted: ['நான்', 'சந்தை', 'வசதி', 'உள்ளது']
Target: [['நான்', 'அந்த', 'சுதிர்காரிப்பு', 'ஆலயத்தின்', 'வெளியே', 'உள்ள', 'சுற்று', 'சாலையில்', 'உள்ளேன்']]
Predicted: ['கால்வின்', 'கிளைன்', 'மீது', 'kerik']
Target: [['கால்வின்', 'கிளைன்', 'கொண்ட', 'கதை', 'இருக்க', 'வேண்டும்', 'என்று', 'மிக்ஸ்']]
Predicted: ['தெளிவு']
Target: [['தெளிவு']]
Predicted: ['போதுமான', 'நன்று']
Target: [['போதுமான', 'நன்று']]
Pre

Predicted: ['ஆ', 'ஆ']
Target: [['ஆ', 'ஆ']]
Predicted: ['அதை', 'செய்ய', 'வேண்டாம்']
Target: [['அதை', 'செய்ய', 'வேண்டாம்']]
Predicted: ['நான்', 'அத', 'எடுத்துக்குறேன்', 'நினைக்கறேன்']
Target: [['நான்', 'அத', 'எடுத்துக்குறேன்']]
Predicted: ['நான்', 'என்', 'fuckin', "'nunchucks"]
Target: [['நான்', 'என்', 'fuckin', "'nunchucks", 'கிடைத்தது']]
Predicted: ['நான்', 'ஒருரேஸர்பிளேடுகொண்டுஇலவசகேன்வாஸ்வெட்டி', 'தெளிவில்லாத']
Target: [['நான்', 'ஒருரேஸர்பிளேடுகொண்டுஇலவசகேன்வாஸ்வெட்டி', 'தெளிவில்லாத']]
Predicted: ['உங்கள்', 'மட்டமான', 'கைகள்', 'என்னை', 'offa']
Target: [['உங்கள்', 'மட்டமான', 'கைகள்', 'என்னை', 'offa', 'போ']]
Predicted: ['ஆமாம்', 'நான்', 'உண்மையில்', 'சமீபத்தில்', 'நிறைய']
Target: [['ஆமாம்', 'நான்', 'உண்மையில்', 'சமீபத்தில்', 'நிறைய', 'யோசித்து', 'வருகின்றன']]
Predicted: ['சீக்கிரம்']
Target: [['சீக்கிரம்', 'மக்கள்', 'கண்டுபிடிப்பாங்க']]
Predicted: ['நான்', 'வழிமுறைகளை', 'பேச']
Target: [['நான்', 'அந்த', 'செய்தியை', 'கண்டெடுத்தேன்']]
Predicted: ['பிரெஞ்சு', 'பேசும்']
Target: [['பிரெஞ

Predicted: ['ஆமாம்']
Target: [['yaah']]
Predicted: ['அவங்க', 'இப்படி', 'அவங்க', 'நாட்டின்', 'பக்கத்து', 'விலை']
Target: [['ஆங்கிலேயர்கள்', 'மற்றும்', 'jamaicans', 'அவர்கள்', 'இந்த', 'குறிப்புகளை', 'அனுப்ப', 'வேண்டாம்']]
Predicted: ['அவள்', 'உயிருடன்', 'இருக்கிறாளா']
Target: [['அவள்', 'உயிருடன்', 'இருக்கிறாளா']]
Predicted: ['அடடா', 'நிஞ்ஜாக்களும்']
Target: [['அடடா', 'நிஞ்ஜாக்களும்']]
Predicted: ['அவரை', 'பொருட்படுத்த', 'வேண்டாம்']
Target: [['அவரை', 'பொருட்படுத்த', 'வேண்டாம்']]
Predicted: ['ஆமாம்']
Target: [['ஆமாம்']]
Predicted: ['மேன்', 'அவனை', 'வெளியேற்று']
Target: [['மேன்', 'அவனை', 'வெளியேற்று']]
Predicted: ['நீங்கள்', 'பவுலா', 'சந்தித்தார்']
Target: [['நீங்கள்', 'பவுலா', 'சந்தித்தார்']]
Predicted: ['வெற்றிட', 'whirring']
Target: [['வெற்றிட', 'whirring']]
Predicted: ['நான்', 'ஓவியம்', 'எடுத்து']
Target: [['நான்', 'ஓவியம்', 'எடுத்து']]
Predicted: ['சரி', 'பெரும்']
Target: [['சரி', 'பெரும்']]
Predicted: ['அது', 'விஷயம்', 'சில', 'கொடுமை', 'துளி', 'கீழே', 'என்று', 'ஆனால்', 'அடைய', 'முட

Predicted: ['எங்களிடம்ஆதாரம்உள்ளது']
Target: [['எங்களிடம்ஆதாரம்உள்ளது']]
Predicted: ['வாழ்க்கை', 'பற்றி', 'புவிஈர்ப்பு', 'புவிஈர்ப்பு', 'கிரகத்தின்', 'தடையாக', 'உள்ளது']
Target: [['அங்கு', 'அதிக', 'மக்களை', 'அனுப்ப', 'நமக்கு', 'தடையாக', 'உள்ளது', 'புவிஈர்ப்பே']]
Predicted: ['பெயர்', 'எட்டு', 'பால்', 'செல்லும்', 'போன்ற', 'ரைட்']
Target: [['பெயர்', 'எட்டு', 'பால்', 'விளையாட்டு', 'போன்ற']]
Predicted: ['நீங்கள்', 'எவ்வளவு', 'நேரம்', 'தெரியாது']
Target: [['நீங்கள்', 'எவ்வளவு', 'நேரம்', 'தெரியாது']]
Predicted: ['இது', 'நம்பிக்கைகள்', 'உள்ளது']
Target: [['இந்த', 'வாழ்க்கை', 'என்ன', 'நாங்கள்', 'இங்கே', 'ஏன்', 'இந்த', 'இல்லை', 'இணைக்க']]
Predicted: ['நீங்கள்', 'அதை', 'மேற்கொள்ளப்படுகின்றன']
Target: [['நீங்கள்', 'அதை', 'மேற்கொள்ளப்படுகின்றன']]
Predicted: ['manஉருதுபேசும்', 'எழுத்துரு']
Target: [['manஉருதுபேசும்', 'எழுத்துரு']]
Predicted: ['நீங்கள்', 'சோர்போனில்', 'மீது', 'நாள்', 'முழுவதும்', 'ஆகிறது', 'இரட்டை', 'சரக்கு', 'உள்ளது', 'நல்லது']
Target: [['நீங்கள்', 'செய்ய', 'வேலை', 'இருக்க', '

(0.5525772151964566,
 0.4497809604168463,
 0.35950989982344894,
 0.27104144246580164)

In [85]:
evaluate_model(encoder, decoder, X_test, Y_test, TAM.index_word)

Predicted: ['நீங்கள்', 'ஹலோ', 'அவளிடம்', 'எடுக்க', 'வேண்டும்', 'இடத்தையும்', 'சொல்லுங்கள்', 'இடத்தையும்', 'தயவு', 'செய்து', 'எங்கள்', 'கூறுவதை', 'ஆக', 'நடக்க', 'கதைய', 'மருத்துவர்']
Target: [['நீங்கள்', 'எங்களுக்கு', 'கோப்ரா', 'என்ற', 'சொல்கிறேன்', 'அல்லது', 'die', 'நீ', 'நம்', 'மாஸ்டர்', 'கொல்ல', 'அதே', 'வாள்']]
Predicted: ['அவர்கள்', 'முக்கிய', 'வாயில்', 'ஒரு', 'கரோக்கி', 'ஒரு', 'என்னநடக்கிறது', 'ஒரு', 'ஆச்சு']
Target: [['அவர்கள்', 'அதே', 'படுக்கை', 'அதே', 'எழுந்து', 'அதே', 'மன', 'ஒரு', 'எரிவாயு', 'நிலையம்']]
Predicted: ['ஒரே', 'கணம்', 'யாரையும்', 'இன்றிரவு', 'நாயகன்', 'ஏதாவது', 'ஒலிகள்', 'சொல்ல', 'மாட்டீர்களா']
Target: [['என்ன', 'அன்று', 'இரவு', 'என்ன', 'நடந்தது', 'மறக்க', 'ஒரே', 'ஒரு', 'கணம்', 'இருந்தது']]
Predicted: ['இஸ்தார்', 'நான்', 'இந்த', 'நினைக்கிறேன்', 'உலகின்', 'இருக்கும்']
Target: [['நீல்ஸ்', 'வேண்டும்', 'அடுத்த', 'எப்படியோ', 'நான்', 'பழைய', 'கொட்டகையின்', 'வேண்டும்', 'எல்', 'செய்']]
Predicted: ['ஆனால்', 'பின்னர்', 'அவங்க', 'மாதிரி', 'வாவ்', 'இல்ல']
Target: [['செம்

Predicted: ['நான்', 'உங்கள்', 'அப்பா', 'செலுத்த', 'என்ன', 'சொல்வேன்']
Target: [['நான்', 'உங்கள்', 'மகன்', 'ஏற்றுக்கொள்ள', 'கெஞ்ச', 'யார்', 'உங்கள்', 'இதயத்தில்', 'உங்களுக்கு', 'தெரியும்', 'வேண்டும்', 'உங்களுடையது']]
Predicted: ['தெரியாது', 'மனித', 'மனித', 'சொந்த', 'வாள்', 'பயன்படுத்தப்படும்']
Target: [['கோயா', 'நவீன', 'கலை', 'தந்தை', 'மனித', 'மனதில்', 'முதல்', 'பெரிய']]
Predicted: ['அந்த', '12', 'மணி', 'நேர', 'நேர', 'நேர', 'வேலை', 'மற்றும்', 'இயங்கும்', 'இயங்கும்', 'இயங்கும்']
Target: [['நாள்', 'மூன்று', 'மூலம்', 'அவர்', 'ஏற்கனவே', 'எப்படியாவது', 'வரை', 'உட்கார்ந்து', 'மற்றும்', 'சுவரில்']]
Predicted: ['நாம்', 'எவ்வளவு', 'வாரங்களுக்கு', 'வண்டி', 'ஒவ்வொரு', 'நிறுவனத்தின்', 'உள்ளது']
Target: [['நீங்கள்', 'திரும்ப', 'வருடங்கள்', 'ஆகும்', 'என்றால்', 'அந்த', 'நேரத்தை', 'நான்', 'ஈர்ப்பின்', 'மீதான', 'ஆராய்வில்']]
Predicted: ['என்றால்', 'கடவுள்', 'ஏற்கனவே', 'சிரிக்க', 'ஆன்லைன்', 'போது', 'எங்களுக்கு', 'பொறுத்தவரை', 'நாம்', 'கற்பனை', 'பக்கத்தில்', 'இருக்கும்']
Target: [['கடவுள்', 'நம்மை',

Predicted: ['ஜார்ஜ்', 'பரவாயில்லை', 'சேகரிக்க', 'இழந்த', 'சேகரிக்க']
Target: [['morel', 'இனி', 'greely', 'மரணம்', 'நம்மை', 'திரும்பி', 'அறிய', 'முடியும்', 'என்று', 'எந்த', 'வாய்ப்பு', 'எடுக்கவில்லை']]
Predicted: ['ஒரு', 'நினைக்கிறேன்']
Target: [['நாம்', 'தெற்கு', 'புல்வெளியில்', 'ஒரு', 'சி', 'கிடைத்துவிட்டது', 'மற்றும்', 'வட', 'மீது', 'ஒரு']]
Predicted: ['நமக்கு', 'பாதுகாப்பான', 'இடம்', 'சட்டவிரோத', 'கிடைக்கும்']
Target: [['நாங்கள்', 'மக்கள்', 'நிறைய', 'இருந்து', 'இரகசியங்களை', 'வைத்து', 'நம்மை', 'நாமே', 'இருந்து', 'அவற்றை', 'வைத்து', 'அனைத்து', 'ஆனால்', 'பெரும்பாலான']]
Predicted: ['அவள்', 'உணவு', 'தேவை', 'அவர்', 'என்னை', 'நீங்கள்', 'இன்னும்', 'வேண்டும்']
Target: [['அவள்', 'உன்னுடன்', 'இருக்க', 'நீங்கள்', 'அவளுக்கு', 'தேவை', 'அவளை', 'ஏதாவது', 'கொடுத்து', 'இருக்க', 'வேண்டும்']]
Predicted: ['பறவைகள்', '100', 'கூறுகிறார்', 'இங்கே', 'நல்ல', 'கூட்டம்', 'அறிக்கை', 'தான்']
Target: [['நாம்', 'இங்கே', 'பார்க்க', 'முடியும்', 'என', 'நல்ல', 'செய்தி', 'கட்டிகள்', 'முற்றிலும்', 'போய்விட்டன', 'என்

Predicted: ['சரி', 'அவனுடைய', 'முதல்ல', 'செலவு', 'நீ', 'சொல்றது', 'அவங்க', 'இருக்காங்க', 'இஸ்தார்']
Target: [['சரி', 'அந்த', 'விசயத்துல', 'நான்', 'நீ', 'இங்க', 'வர', 'இந்த', 'ராக்']]
Predicted: ['தங்கள்', 'ஒரு', 'குப்பை', 'நீல', 'கொள்கைகளை', 'நாம்', 'மோதிரத்தை', 'வேண்டும்']
Target: [['நாம்', 'வெள்ளை', 'மாளிகை', 'எல்லையை', 'பெற்று', 'விட்டேன்', 'மற்றும்', '10', 'தொகுதி', 'அகற்றப்படும்']]
Predicted: ['மன்னிக்கவும்', 'பெயர்', 'மாடிக்கு', 'சாம்', 'ஒரு', 'பெயர்', 'வேலை', 'அவரது', 'அதுதான்', 'வாழ்க்கை', 'இருப்பாய்']
Target: [['உரிமையாளர்', 'திருமதி', 'லில்லி', 'அவர்', 'இந்த', 'பெயர்', 'அவரது', 'பிளாட்', 'மாற்றப்பட்டது']]
Predicted: ['அவர்', 'இங்கு', 'ஒரு', 'என்', 'பெயரை', 'திருடியது', 'என்னை', 'பற்றி', 'நம்ப', 'வேண்டும்']
Target: [['அவர்', 'என்னை', 'அங்கு', 'ஒரு', 'புத்தகம்', 'பெற', 'ஒரு', 'சில', 'உதவிகள்', 'பணம்', 'இருந்தது']]
Predicted: ['நான்', 'என்ன', 'செய்ய', 'தெரியாது', 'என்பதை', 'என்ன', 'என்பதை', 'செய்ய', 'வேண்டும்']
Target: [['ஏனென்றால்', 'அங்கு', 'செல்வது', 'என்', 'நான்', 'அதனை',

Predicted: ['அந்த', 'நஷ்டம்', 'வெள்ளை', 'மனித', 'பணம்', 'மற்ற', 'மோசமான', 'குறைந்து', 'புரட்சி', 'இல்லை', 'உணவு', 'உணவு', 'உணவு', 'உணவு', 'உணவு', 'பணம்', 'வாங்க', 'கேளு', 'ன்']
Target: [['வெப்பமான', 'மத்திய', 'ரிசர்வ்', 'இருந்து', 'நிதி', '7', '7', 'டிரில்லியன்', 'நிதி', 'நிறுவனங்கள்', 'போராடி', 'பெற']]
Predicted: ['யே', 'இன்னொரு', 'ஒவ்வொரு', 'நல்ல', 'மக்கள்', 'நீ', 'சொல்ல', 'போற', 'இன்னொரு', 'மருத்துவமனை']
Target: [['நாயகன்', 'நீங்கள்', 'என்றாவது', 'ஒருவேளை', 'நான்', 'நினைக்கிறேன்', 'எல்லோரும்', 'அதே', 'நேரத்தில்', 'பள்ளி', 'போகலாமா']]
Predicted: ['நான்', 'நினைக்கிறேன்', 'என்று', 'நான்', 'உன்', 'பைத்தியம்', 'என்று', 'ஆனால்', 'நான்', 'அவர்களை', 'கேட்க', 'போது', 'வது']
Target: [['நான்', 'உனக்கு', 'பயம்', 'நினைக்கிறேன்', 'அது', 'இருக்கும்', 'போது', 'மேல்', 'உங்கள்', 'இதயம்']]
Predicted: ['ஒரு', 'பொண்ணு', 'எனக்கு', 'தெரியாது']
Target: [['பார்', 'நான்', 'ஒரு', 'பெண்', 'தோழி', 'இல்லை', 'நான்', 'ஒரு', 'குடும்ப', 'இல்லை']]
Predicted: ['அவங்க', 'ஜூலியா', 'சந்தித்து', 'சந்தித்து', 'துளி

...

Predicted: ['வின்சென்ட்', 'நான்', 'அழகான', 'நாள்', 'ஒரு', 'அழகான', 'விபத்து', 'பத்தி', 'சொல்ல', 'கிடைக்க', 'உங்கள்', 'மிஸ்டர்', 'படுத்து', 'என்ன', 'கிடைக்க', 'நாம்']
Target: [['ஆமாம்', 'வின்சென்ட்', 'நீ', 'என்ன', 'நான்', 'உன்னோட', 'போன', 'வார', 'நான்']]
Predicted: ['நரகம்', 'கிருப்டான்', 'greely', 'இராணுவ', 'அறியப்படுகிறது']
Target: [['உங்க', 'வீட்டை', 'வாங்கும்', 'உரிமை', 'அதை', 'அவங்க', 'அவர்களின்', 'புதிய', 'கனவு']]
Predicted: ['அது', 'நீ', 'ஆனால்', 'அது', 'உண்மையில்', 'அது', 'மேலும்', 'உங்கள்', 'உண்மையில்', 'ஏனெனில்', 'உள்ளது', 'ஏனெனில்', 'அவருக்கு', 'உயிருடன்', 'உள்ளது']
Target: [['நடக்கப்போவதில்லை', 'ஆனால்', 'நான்', 'உங்கள்', 'ஆவி', 'பிடிக்கும்', 'அந்த', 'சாமுராய்', 'விஷயம்', 'அந்த', 'இது', 'நன்றாக', 'இருக்கிறது']]
Predicted: ['நாம்', 'சொல்வதை', 'நாம்', 'நினைக்கிறீர்கள்', 'என்று', 'மேலும்', 'நன்றாக', 'உள்ளது', 'என்று']
Target: [['மேலும்', 'நாம்', 'கேட்டு', 'வருகிறோம்', 'என்று', 'பாகங்கள்', 'இருந்தால்', 'நாம்', 'கீழே', 'இங்கே', 'ஒரு', 'குழுவினர்', 'இயங்கும்']]
Predicted: ['புது'

Predicted: ['நான்', 'கண்கள்', 'பகுதிகளில்', 'தேட', 'கூறுகிறோம்']
Target: [['நீ', 'உண்மையை', 'உணர்ந்து', 'எப்படி', 'வந்தது', 'ஏன்', 'வந்தது', 'என', 'ஆராய', 'வேண்டும்', 'அப்படி', 'நீ', 'ஒரு', 'முடிவிற்கு', 'வர', 'வேண்டும்']]
Predicted: ['நான்', 'என்', 'நாம்', 'வேகமா', 'விற்க', 'வேண்டும்']
Target: [['நாம்', 'இன்று', 'எங்கள்', 'குடும்பம்', 'சந்திக்க', 'கூடும்', 'ஆனால்', 'ஒன்று', 'நான்', 'என்', 'உள்ள', 'விரும்பவில்லை']]
Predicted: ['நான்', 'நினைக்கிறேன்', 'என்று', 'நான்', 'உன்', 'பைத்தியம்', 'என்று', 'ஆனால்', 'நான்', 'அவர்களை', 'கேட்க', 'போது', 'வது']
Target: [['நான்', 'உனக்கு', 'பயம்', 'நினைக்கிறேன்', 'அது', 'இருக்கும்', 'போது', 'மேல்', 'உங்கள்', 'இதயம்']]
Predicted: ['இல்ல', 'அவள்', 'அவங்க', '35', 'வராங்க', 'அவங்க', 'ஜூலியா', 'இரண்டாவதுபிடித்து', 'மீண்டு', 'வா']
Target: [['அவர்', 'சாண்ட்ரா', 'பிரிஸ்டல்', 'வாழ்க்கை', 'எடுத்து', 'மீண்டும்', 'தனது', '13', 'முறை', 'மார்பு', 'மற்றும்']]
Predicted: ['எந்த', 'பணம்', 'செய்ய', 'அவசியம்', 'கடைசி', 'ஒப்பந்தம்', 'செய்ய', 'எந்த', 'ஒப்பந்தத்துல', 'வர

Predicted: ['இந்த', 'விஷயம்', 'ஓ', 'நாம', 'விண்வெளி', 'கடினமான', 'புணர்கிறேன்']
Target: [['ஒரு', 'புணர்கிறேன்', 'சென்டர்', 'அல்லது', 'சில', 'புல்ஷிட்', 'கட்ட', 'morel', 'கீழே', 'இந்த', 'இடத்தில்', 'எரிக்க', 'போகிறேன்', 'இருந்தது']]
Predicted: ['நான்', 'ஒரு', 'வெள்ளி', 'ஒரு', 'நேற்றிரவு', 'வந்தது', 'அந்த', 'கூட்டம்', 'வேண்டும்']
Target: [['அவர்', 'குழந்தை', 'ஜாக்', 'அவர்', 'ஐந்து', 'அவரது', 'சான்றுகள்', 'கோப்பு', 'கொடுத்தார்', 'எனவே', 'இது', 'அனைத்து', 'நாம்', 'ஒரு', 'செலுத்தி', 'அந்த']]
Predicted: ['பாருங்கள்', 'நான்', 'இந்த', 'பையன்', 'சரியா', "there'sa", 'சரியா']
Target: [['ஒரு', 'நான்', 'இந்த', 'பையன்', 'யார்', 'என்று', 'தெரியவில்லை', 'பாருங்கள்', 'அது', 'தான்', 'இருக்கிறது']]
Predicted: ['நாம்', 'நீண்ட', 'காலம்', 'முன்பு', 'கிடைத்தது', 'போது', 'அவர்', 'நாம்', 'அதை', 'செய்ய']
Target: [['நாங்கள்', 'அவள்', 'இன்னும்', 'மூச்சு', 'அவரது', 'அடக்கம்', 'சென்ற', 'போது', 'மட்டும்', 'தான்', 'இருந்தது']]
Predicted: ['நான்', 'உங்கள்', 'மனிதன்', 'காதல்', 'பெற', 'amelia']
Target: [['உங்களுக்க

Predicted: ['நாம்', 'விரல்', 'நீங்கள்', 'நினைவில்', 'கொள்ள', 'மாட்டேன்', 'என்று', 'ஒரு', 'தெரியாது']
Target: [['எப்படி', 'நீங்கள்', 'ஒரு', 'நாள்', 'இல்லையா', 'அமெரிக்காவின்', 'எதிராக', 'செயல்பட']]
Predicted: ['ரொம்ப', 'நான்', 'பேச', 'முடியும்', 'வலுவான', 'அறிவார்ந்த', 'இருக்கிறது', 'என்று', 'ஒரு', 'நல்ல', 'குடும்பம்', 'சொந்தமானது']
Target: [['நீ', 'அவரை', 'அங்கு', 'கிடைக்கும்', 'என்று', 'நீங்கள்', 'சார்லஸ்டன்', 'நாளை', 'அவரை', 'கிடைக்கும்', 'என்று', 'மிகவும்', 'முக்கியமானது', 'பாருங்கள்']]
Predicted: ['எங்களுக்கு', 'ஒரு', 'நல்ல', 'தொழில்', 'பயன்படுத்தப்படுகின்றன', 'என்று', 'தெரிய', 'வேண்டும்', 'இரத்த']
Target: [['அந்த', 'நம்பிக்கை', 'உள்ள', 'பொதிந்துள்ள', 'அடிப்படை', 'நம்பிக்கை', 'ஒவ்வொரு', 'நபரின்', 'திறன்', 'உள்ள', 'நல்ல', 'ஒரு', 'சக்தியாக', 'இருக்க', 'வேண்டும்']]
Predicted: ['நாம்', 'நீண்ட', 'காலம்', 'முன்பு', 'கிடைத்தது', 'போது', 'அவர்', 'நாம்', 'அதை', 'செய்ய']
Target: [['நாங்கள்', 'அவள்', 'இன்னும்', 'மூச்சு', 'அவரது', 'அடக்கம்', 'சென்ற', 'போது', 'மட்டும்', 'தான்', 'இருந்தது

(0.1158326319935706,
 0.03229213238510325,
 0.010372718783558563,
 0.004080211733623626)